In [1]:
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.express as px
import numpy as np
from dashboard.graphs import plot_cost_storage_scenarios, plot_storage_results
from dashboard.data import (
    get_storage_results,
    get_storage_scenario_options,
    calculate_cost_storage_scenarios,
)

2024-03-14 16:37:08.327 WARNING streamlit.runtime.caching.cache_data_api: No runtime found, using MemoryCacheStorageManager
2024-03-14 16:37:08.330 WARNING streamlit.runtime.caching.cache_data_api: No runtime found, using MemoryCacheStorageManager
2024-03-14 16:37:08.332 WARNING streamlit.runtime.caching.cache_data_api: No runtime found, using MemoryCacheStorageManager
2024-03-14 16:37:08.334 WARNING streamlit.runtime.caching.cache_data_api: No runtime found, using MemoryCacheStorageManager
2024-03-14 16:37:08.335 WARNING streamlit.runtime.caching.cache_data_api: No runtime found, using MemoryCacheStorageManager
2024-03-14 16:37:08.338 WARNING streamlit.runtime.caching.cache_data_api: No runtime found, using MemoryCacheStorageManager
2024-03-14 16:37:08.339 WARNING streamlit.runtime.caching.cache_data_api: No runtime found, using MemoryCacheStorageManager
2024-03-14 16:37:08.341 WARNING streamlit.runtime.caching.cache_data_api: No runtime found, using MemoryCacheStorageManager
2024-03-

In [2]:
fn_results = "./data/results_storage.parquet"
# fn_results = (
#     "https://jabspublicbucket.s3.eu-central-1.amazonaws.com/results_storage.parquet"
# )

In [34]:
def get_storage_results(fn: str, country: str, start: str) -> pd.DataFrame:
    """Get results from storage model

    Args:
        fn: name of file with results
        country: country to filter
        start: start date to filter
    """
    df = pd.read_parquet(
        fn,
        filters=[
            ("country", "==", country),
            ("start", "==", start),
        ],
    ).drop(["start", "end", "country"], axis=1)

    return df
df = get_storage_results(fn_results, country="DE", start="2017/06/01 00:00").query("scenario == 'storageOnly' and share_renewable == 1.0")
idx = ["share_renewable", "scenario", "date"]
test = df.set_index(idx)[["base", "wind", "solar", "netStorage"]].sum(1) - df.set_index(idx)["demand"]
df[idx + ["demand", "netStorage", "base", "wind", "solar"]].to_clipboard()

In [4]:
cost = {
    "storage": 10000,
    "wind": 1,
    "solar": 1,
    "base": 2
}
df = get_storage_results(fn_results, country="DE", start="2017/06/01 00:00")
df = df.merge(calculate_cost_storage_scenarios(df, cost), on=["scenario", "share_renewable"])
plot_cost_storage_scenarios(df)

2024-03-14 16:37:21.753 No runtime found, using MemoryCacheStorageManager
2024-03-14 16:37:22.269 No runtime found, using MemoryCacheStorageManager


In [25]:

fig = plot_storage_results(df)
fig.show()

In [20]:
re_levels = [i/10 for i in range(11)]
print(df.share_renewable.unique(), re_levels)
df.assign(share_renewable=lambda df: df["share_renewable"].round(2)).query(f"share_renewable in {re_levels}").share_renewable.unique()

[0.   0.01 0.02 0.03 0.04 0.05 0.06 0.07 0.08 0.09 0.1  0.11 0.12 0.13
 0.14 0.15 0.16 0.17 0.18 0.19 0.2  0.21 0.22 0.23 0.24 0.25 0.26 0.27
 0.28 0.29 0.3  0.31 0.32 0.33 0.34 0.35 0.36 0.37 0.38 0.39 0.4  0.41
 0.42 0.43 0.44 0.45 0.46 0.47 0.48 0.49 0.5  0.51 0.52 0.53 0.54 0.55
 0.56 0.57 0.58 0.59 0.6  0.61 0.62 0.63 0.64 0.65 0.66 0.67 0.68 0.69
 0.7  0.71 0.72 0.73 0.74 0.75 0.76 0.77 0.78 0.79 0.8  0.81 0.82 0.83
 0.84 0.85 0.86 0.87 0.88 0.89 0.9  0.91 0.92 0.93 0.94 0.95 0.96 0.97
 0.98 0.99 1.  ] [0.0, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1.0]


array([0. , 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1. ])